## Introduction

The Notebook below includes Three Sections that comprises the entire Week Three Peer Graded assignment, "Segmenting and Clustering Neighborhoods in Toronto":
The notebook includes seven tasks:

(1.) Scraping of a Wikipedia page: https://en.wikipedia.org/wiki/List_of_postal_codes_of_Canada:_M for the Toronto neighborhood data using the BeautifulSoup package

(2.) Creating a Panda Dataframe from the data that will consist of three columns, PostalCode, Borough and Neighborhood.

(3.) Preprocess & clean the data where Boroughs that are not assigned will be ignored; then combine comma separated neighborhoods per PostalCode.

(4.) Generate maps to visualize the neighborhoods.

(5.) Insertion of descriptive Markdown cells throughout.

(6.) Get latitude and Longitude data for each neighborhood, using the Python Geocoder package, in order to utilize the FourSquare location data.

(7.) The exploration and clustering of neighborhoods in Toronto Canada.


## Section 1 of 3

In [ ]:
from bs4 import BeautifulSoup
import lxml

import numpy as np # library to handle data in a vectorized manner
import pandas as pd # library for data analsysis
pd.set_option('display.max_columns', None)
pd.set_option('display.max_rows', None)

import json # library to handle JSON files

!conda install -c conda-forge geopy --yes # uncomment this line if you haven't completed the Foursquare API lab
from geopy.geocoders import Nominatim # convert an address into latitude and longitude values

import requests # library to handle requests
from pandas.io.json import json_normalize # tranform JSON file into a pandas dataframe

# Matplotlib and associated plotting modules
import matplotlib.cm as cm
import matplotlib.colors as colors

# import k-means from clustering stage
from sklearn.cluster import KMeans
from sklearn.datasets.samples_generator import make_blobs

#!conda install -c conda-forge folium=0.5.0 --yes # uncomment this line if you haven't completed the Foursquare API lab
import folium # map rendering library

from bs4 import BeautifulSoup
import lxml

print('Libraries imported.')

#### Scrape the Toronto neighborhood data using the BeautifulSoup package

In [5]:
List_url = "https://en.wikipedia.org/wiki/List_of_postal_codes_of_Canada:_M"
source = requests.get(List_url).text
soup = BeautifulSoup(source, 'xml')
table=soup.find('table')

#### Creating a Panda Dataframe from the data that includes three columns: PostalCode, Borough and Neighborhood

In [6]:
column_names = ['Postalcode','Borough','Neighborhood']
df = pd.DataFrame(columns = column_names)

#### Loop through the data for each set of PostalCode, Borough and Neighborhood and show the first 5 rows

In [7]:
for tr_cell in table.find_all('tr'):
    row_data=[]
    for td_cell in tr_cell.find_all('td'):
        row_data.append(td_cell.text.strip())
    if len(row_data)==3:
        df.loc[len(df)] = row_data
df.head()

Postalcode           Borough      Neighborhood
0        M1A      Not assigned      Not assigned
1        M2A      Not assigned      Not assigned
2        M3A        North York         Parkwoods
3        M4A        North York  Victoria Village
4        M5A  Downtown Toronto      Harbourfront

#### Prepocessing the data to ignore Boroughs that are not assigned and show the first 5 rows.

In [8]:
df=df[df['Borough']!='Not assigned']

In [9]:
df.head()

Postalcode           Borough      Neighborhood
2        M3A        North York         Parkwoods
3        M4A        North York  Victoria Village
4        M5A  Downtown Toronto      Harbourfront
5        M6A        North York  Lawrence Heights
6        M6A        North York    Lawrence Manor

#### Combine comma separated neighborhoods per PostalCode and show the first 5 rows.

In [10]:
temp_df=df.groupby('Postalcode')['Neighborhood'].apply(lambda x: "%s" % ', '.join(x))
temp_df=temp_df.reset_index(drop=False)
temp_df.rename(columns={'Neighborhood':'Neighborhood_joined'},inplace=True)

df_combine = pd.merge(df, temp_df, on='Postalcode')

df_combine.drop_duplicates(inplace=True)

df_combine.rename(columns={'Neighborhood_joined':'Neighborhood'},inplace=True)

df_combine.head()

Postalcode           Borough      Neighborhood  \
0        M3A        North York         Parkwoods   
1        M4A        North York  Victoria Village   
2        M5A  Downtown Toronto      Harbourfront   
3        M6A        North York  Lawrence Heights   
4        M6A        North York    Lawrence Manor   

                       Neighborhood  
0                         Parkwoods  
1                  Victoria Village  
2                      Harbourfront  
3  Lawrence Heights, Lawrence Manor  
4  Lawrence Heights, Lawrence Manor

#### Calling .shape method to print the number of rows in the dataframe

In [11]:
df_combine.shape

(210, 4)

## Section 2 of 3

#### Installing and importing geocoder

In [ ]:
import sys
!{sys.executable} -m pip install geocoder

print('Packages installed.')

In [13]:
import geocoder 

#### Getting latitude and longitude coordinates for each neighborhood

In [14]:
URL = "https://www.wikizeroo.org/index.php?q=aHR0cHM6Ly9lbi53aWtpcGVkaWEub3JnL3dpa2kvTGlzdF9vZl9wb3N0YWxfY29kZXNfb2ZfQ2FuYWRhOl9N"
r = requests.get(URL) 
  
soup = BeautifulSoup(r.content, 'html5lib') 
table = soup.find('div', attrs = {'id':'container'}) 


print('wikizeroo page scraped for coordinates.')

wikizeroo page scraped for coordinates.


#### Collecting the data for the dataframe

In [15]:
postalCodes = [];
boroughs= [];
neighborhoods = [];
columnNum = 1;
passVal = False

for row in soup.find_all('td'):
    for cell in row:
        if cell.string and cell.string[0].isalpha() and len(cell.string) > 2:
            passVal = False
            if columnNum == 1:
                if passVal == False and cell.string[1].isdigit():
                    postalCodes.append(cell.string);   
                    columnNum = 2
                else:
                    continue
            elif columnNum == 2 :
                if cell.string == 'Not assigned':
                    passVal = True
                    del postalCodes[-1]
                    columnNum = 1
                    continue
                else:
                    boroughs.append(cell.string);      
                    columnNum = 3
            elif columnNum == 3 :
                if cell.string == 'Not assigned\n':
                    neighborhoods.append(boroughs[-1])
                else:
                    neighborhoods.append(cell.string); 
                columnNum = 1
                
print('Data collected for dataframe.')

Data collected for dataframe.


#### Define the columns for the MyNeighbors dataframe

In [16]:
# define MyNeighbors dataframe columns
column_names = ['PostalCode', 'Borough', 'Neighborhood', 'Latitude', 'Longitude'] 

# instantiate the dataframe
MyNeighbors = pd.DataFrame(columns=column_names)

MyNeighbors

Empty DataFrame
Columns: [PostalCode, Borough, Neighborhood, Latitude, Longitude]
Index: []

#### Loop through the data and fill the dataframe one row at a time.

In [17]:
lat_lng_coords = None

for data in range(0, len(postalCodes)-1):
    code = postalCodes[data]
    borough = boroughs[data]
    neighborhood_name = neighborhoods[data]
    
    g = geocoder.arcgis('{}, Toronto, Ontario'.format(code))
    lat_lng_coords = g.latlng

    MyNeighbors = MyNeighbors.append({ 'PostalCode': code,
                                   'Borough': borough,
                                   'Neighborhood': neighborhood_name,
                                   'Latitude': lat_lng_coords[0],
                                   'Longitude': lat_lng_coords[1]}, ignore_index=True)
    
MyNeighbors.head()

PostalCode           Borough      Neighborhood   Latitude  Longitude
0        M3A        North York         Parkwoods  43.752420 -79.329242
1        M4A        North York  Victoria Village  43.730600 -79.313265
2        M5A  Downtown Toronto      Harbourfront  43.650295 -79.359166
3        M6A        North York  Lawrence Heights  43.723270 -79.451286
4        M6A        North York    Lawrence Manor  43.723270 -79.451286

#### Calling .shape method to print the number of rows in the dataframe

In [18]:
MyNeighbors.shape

(209, 5)

#### Making sure the MyNeighbors dataframe has 10 boroughs and 209 neighborhoods

In [19]:
print('The dataframe has {} boroughs and {} neighborhoods.'.format(
        len(MyNeighbors['Borough'].unique()),
        MyNeighbors.shape[0]
    )
)

The dataframe has 10 boroughs and 209 neighborhoods.


#### Use geopy library to get the latitude and longitude values of Toronto CA

In order to define an instance of the geocoder, we need to define a user_agent. We will name our agent Toronto_explorer, as shown below.

In [20]:
address = 'Toronto, CA'

geolocator = Nominatim(user_agent="Toronto_explorer")
location = geolocator.geocode(address)
latitude = location.latitude
longitude = location.longitude
print('The geograpical coordinate of Toronto CA are {}, {}.'.format(latitude, longitude))

The geograpical coordinate of Toronto CA are 43.653963, -79.387207.


#### Create a map, with Folium library methods, of Toronto with neighborhoods superimposed on top

In [21]:
map_toronto = folium.Map(location=[latitude, longitude], zoom_start=10)

# add markers to map
for lat, lng, borough, neighborhood in zip(MyNeighbors['Latitude'], MyNeighbors['Longitude'], MyNeighbors['Borough'], MyNeighbors['Neighborhood']):
    label = '{}, {}'.format(neighborhood, borough)
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='blue',
        fill=True,
        fill_color='#3186cc',
        fill_opacity=0.7,
        parse_html=False).add_to(map_toronto)  
    
map_toronto

#### Define Foursquare Credentials and Version

In [22]:
CLIENT_ID = 'G2IJ5YGRMGABJ00HBETVU0SCBPHDPXXHX2A0JDGHJMHDMIH1' # your Foursquare ID
CLIENT_SECRET = 'TE5P3EX2CNBK0WH2PI14WZWFSVMTFSNYXEPRKYUX3VIYCDPR' # your Foursquare Secret
VERSION = '20200311' # Foursquare API version

print('Your credentails:')
print('CLIENT_ID: ' + CLIENT_ID)
print('CLIENT_SECRET:' + CLIENT_SECRET)

Your credentails:
CLIENT_ID: G2IJ5YGRMGABJ00HBETVU0SCBPHDPXXHX2A0JDGHJMHDMIH1
CLIENT_SECRET:TE5P3EX2CNBK0WH2PI14WZWFSVMTFSNYXEPRKYUX3VIYCDPR


#### Exploring the first neighborhood and return its name

In [23]:
MyNeighbors.loc[0, 'Neighborhood']

'Parkwoods'

Get the latitude and longitude coordinates for Parkwoods

In [24]:
neighborhood_latitude = MyNeighbors.loc[0, 'Latitude']
neighborhood_longitude = MyNeighbors.loc[0, 'Longitude']

neighborhood_name = MyNeighbors.loc[0, 'Neighborhood']

print('Latitude and longitude values of {} are {}, {}.'.format(neighborhood_name, 
                                                               neighborhood_latitude, 
                                                               neighborhood_longitude))

Latitude and longitude values of Parkwoods are 43.75242000000003, -79.32924245299995.


Creating a GET request

In [25]:
LIMIT = 100 # limit of number of venues returned by Foursquare API
radius = 500 # define radius
url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format(
    CLIENT_ID, 
    CLIENT_SECRET, 
    VERSION, 
    neighborhood_latitude, 
    neighborhood_longitude, 
    radius, 
    LIMIT)
url # display URL

'https://api.foursquare.com/v2/venues/explore?&client_id=G2IJ5YGRMGABJ00HBETVU0SCBPHDPXXHX2A0JDGHJMHDMIH1&client_secret=TE5P3EX2CNBK0WH2PI14WZWFSVMTFSNYXEPRKYUX3VIYCDPR&v=20200311&ll=43.75242000000003,-79.32924245299995&radius=500&limit=100'

Test the GET request

In [26]:
results = requests.get(url).json()
results

{'meta': {'code': 200, 'requestId': '5e69251e98205d001b9862c6'},
 'response': {'warning': {'text': "There aren't a lot of results near you. Try something more general, reset your filters, or expand the search area."},
  'headerLocation': 'Parkwoods - Donalda',
  'headerFullLocation': 'Parkwoods - Donalda, Toronto',
  'headerLocationGranularity': 'neighborhood',
  'totalResults': 3,
  'suggestedBounds': {'ne': {'lat': 43.75692000450003,
    'lng': -79.32302427998279},
   'sw': {'lat': 43.74791999550003, 'lng': -79.33546062601711}},
  'groups': [{'type': 'Recommended Places',
    'name': 'recommended',
    'items': [{'reasons': {'count': 0,
       'items': [{'summary': 'This spot is popular',
         'type': 'general',
         'reasonName': 'globalInteractionReason'}]},
      'venue': {'id': '4e8d9dcdd5fbbbb6b3003c7b',
       'name': 'Brookbanks Park',
       'location': {'address': 'Toronto',
        'lat': 43.751976046055574,
        'lng': -79.33214044722958,
        'labeledLatLngs

Since all the information is in the items key we will reuse the get_category_type function from a previous Foursquare lab.

In [27]:
# function that extracts the category of the venue
def get_category_type(row):
    try:
        categories_list = row['categories']
    except:
        categories_list = row['venue.categories']
        
    if len(categories_list) == 0:
        return None
    else:
        return categories_list[0]['name']

Cleaning the json and structure it into a pandas dataframe

In [28]:
venues = results['response']['groups'][0]['items']
    
nearby_venues = json_normalize(venues) # flatten JSON

# filter columns
filtered_columns = ['venue.name', 'venue.categories', 'venue.location.lat', 'venue.location.lng']
nearby_venues =nearby_venues.loc[:, filtered_columns]

# filter the category for each row
nearby_venues['venue.categories'] = nearby_venues.apply(get_category_type, axis=1)

# clean columns
nearby_venues.columns = [col.split(".")[-1] for col in nearby_venues.columns]

nearby_venues.head()

name         categories        lat        lng
0             Brookbanks Park               Park  43.751976 -79.332140
1               Variety Store  Food & Drink Shop  43.751974 -79.333114
2  TTC stop - 44 Valley Woods           Bus Stop  43.755402 -79.333741

Let's check to see how many venues were returned by Foursquare?

In [29]:
print('{} venues were returned by Foursquare.'.format(nearby_venues.shape[0]))

3 venues were returned by Foursquare.


# Section 3 of 3
## Explore & Cluster Toronto Neighborhoods
#### Create a function to repeat the same process to all the neighborhoods

In [32]:
def getNearbyVenues(names, latitudes, longitudes, radius=500):
    
    venues_list=[]
    for name, lat, lng in zip(names, latitudes, longitudes):
        print(name)
            
        # create the API request URL
        url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format(
            CLIENT_ID, 
            CLIENT_SECRET, 
            VERSION, 
            lat, 
            lng, 
            radius, 
            LIMIT)
            
        # make the GET request
        results = requests.get(url).json()["response"]['groups'][0]['items']
        
        # return only relevant information for each nearby venue
        venues_list.append([(
            name, 
            lat, 
            lng, 
            v['venue']['name'], 
            v['venue']['location']['lat'], 
            v['venue']['location']['lng'],  
            v['venue']['categories'][0]['name']) for v in results])

    nearby_venues = pd.DataFrame([item for venue_list in venues_list for item in venue_list])
    nearby_venues.columns = ['Neighborhood', 
                  'Neighborhood Latitude', 
                  'Neighborhood Longitude', 
                  'Venue', 
                  'Venue Latitude', 
                  'Venue Longitude', 
                  'Venue Category']
    
    return(nearby_venues)

####  Code that runs the above function on each neighborhood and create a new dataframe called toronto_venues

In [33]:
toronto_venues = getNearbyVenues(names=MyNeighbors['Neighborhood'],
                                   latitudes=MyNeighbors['Latitude'],
                                   longitudes=MyNeighbors['Longitude']
                                  )

Parkwoods
Victoria Village
Harbourfront
Lawrence Heights
Lawrence Manor
Queen's Park
Islington Avenue
Rouge
Malvern
Don Mills North

Woodbine Gardens
Parkview Hill
Ryerson

Garden District

Glencairn

Cloverdale

Islington
Martin Grove

Princess Gardens
West Deane Park
Highland Creek
Rouge Hill
Port Union
Flemingdon Park
Don Mills South

Woodbine Heights
St. James Town
Humewood-Cedarvale
Bloordale Gardens

Eringate

Markland Wood
Old Burnhamthorpe

Guildwood

Morningside
West Hill
The Beaches
Berczy Park
Caledonia-Fairbanks

Woburn
Leaside
Central Bay Street

Christie

Cedarbrae

Hillcrest Village
Bathurst Manor
Downsview North

Wilson Heights
Thorncliffe Park
Adelaide

King

Richmond

Dovercourt Village
Dufferin

Scarborough Village
Fairview

Henry Farm
Oriole

Northwood Park
York University
East Toronto
Harbourfront East

Toronto Islands
Union Station
Little Portugal
Trinity
East Birchmount Park

Ionview
Kennedy Park
Bayview Village
CFB Toronto
Downsview East

The Danforth West

Rive

#### Checking the size of the resulting dataframe

In [34]:
print(toronto_venues.shape)
toronto_venues.head()

(4733, 7)


Neighborhood  Neighborhood Latitude  Neighborhood Longitude  \
0         Parkwoods               43.75242              -79.329242   
1         Parkwoods               43.75242              -79.329242   
2         Parkwoods               43.75242              -79.329242   
3  Victoria Village               43.73060              -79.313265   
4  Victoria Village               43.73060              -79.313265   

                        Venue  Venue Latitude  Venue Longitude  \
0             Brookbanks Park       43.751976       -79.332140   
1               Variety Store       43.751974       -79.333114   
2  TTC stop - 44 Valley Woods       43.755402       -79.333741   
3                Wigmore Park       43.731023       -79.310771   
4          Memories of Africa       43.726602       -79.312427   

      Venue Category  
0               Park  
1  Food & Drink Shop  
2           Bus Stop  
3               Park  
4      Grocery Store

Checking how many venues were returned for each neighborhood

In [35]:
toronto_venues.groupby('Neighborhood').count()

Neighborhood Latitude  \
Neighborhood                                                                
Adelaide                                                              100   
                                                                       16   
Agincourt                                                               1   
Agincourt North                                                        15   
Albion Gardens                                                          4   
                                                                        1   
Alderwood                                                              68   
Bathurst Manor                                                          4   
Bathurst Quay                                                          15   
                                                                       22   
Bayview Village                                                        60   
Beaumond Heights                                                        6   
Bedford Park                                                            7   
Berczy Park                                                            69   
Birch Cliff                                                           100   
Bloordale Gardens                                                       4   
                                                                       68   
Brockton                                                               37   
                                                                        9   
Business Reply Mail Processing Centre 969 Eastern                     100   
                                                                        1   
CFB Toronto                                                            94   
CN Tower                                                               78   
Cabbagetown                                                            11   
Caledonia-Fairbanks                                                    86   
                                                                       10   
Canada Post Gateway Processing Centre                                  10   
                                                                        6   
Cedarbrae                                                               6   
                                                                        6   
Central Bay Street                                                      1   
                                                                      100   
Chinatown                                                              25   
Christie                                                                7   
                                                                        6   
Church and Wellesley                                                    5   
Clairlea                                                              100   
Clarks Corners                                                          3   
                                                                        7   
Cliffcrest                                                              4   
Cliffside                                                              18   
Cliffside West                                                          3   
                                                                        2   
Cloverdale                                                              4   
                                                                        1   
Commerce Court                                                         21   
Davisville                                                             12   
                                                                       18   
Davisville North                                                        4   
                                                                        4   
Deer Park                                       

Discover out how many unique categories can be curated from all the returned venues

In [36]:
print('There are {} uniques categories.'.format(len(toronto_venues['Venue Category'].unique())))

There are 262 uniques categories.


### Analyze Each Neighborhood

In [39]:
# one hot encoding
toronto_onehot = pd.get_dummies(toronto_venues[['Venue Category']], prefix="", prefix_sep="")

# add neighborhood column back to dataframe
toronto_onehot['Neighborhood'] = toronto_venues['Neighborhood'] 

# move neighborhood column to the first column
fixed_columns = [toronto_onehot.columns[-1]] + list(toronto_onehot.columns[:-1])
toronto_onehot = toronto_onehot[fixed_columns]

toronto_onehot.head()

Yoga Studio  Afghan Restaurant  Airport  American Restaurant  Antique Shop  \
0            0                  0        0                    0             0   
1            0                  0        0                    0             0   
2            0                  0        0                    0             0   
3            0                  0        0                    0             0   
4            0                  0        0                    0             0   

   Art Gallery  Arts & Crafts Store  Asian Restaurant  Athletics & Sports  \
0            0                    0                 0                   0   
1            0                    0                 0                   0   
2            0                    0                 0                   0   
3            0                    0                 0                   0   
4            0                    0                 0                   0   

   Auto Dealership  Auto Garage  BBQ Joint  Baby Store  Badminton Court  \
0                0            0          0           0                0   
1                0            0          0           0                0   
2                0            0          0           0                0   
3                0            0          0           0                0   
4                0            0          0           0                0   

   Bagel Shop  Bakery  Bank  Bar  Basketball Court  Basketball Stadium  \
0           0       0     0    0                 0                   0   
1           0       0     0    0                 0                   0   
2           0       0     0    0                 0                   0   
3           0       0     0    0                 0                   0   
4           0       0     0    0                 0                   0   

   Beer Bar  Beer Store  Belgian Restaurant  Bike Shop  Bistro  Boat or Ferry  \
0         0           0                   0          0       0              0   
1         0           0                   0          0       0              0   
2         0           0                   0          0       0              0   
3         0           0                   0          0       0              0   
4         0           0                   0          0       0              0   

   Bookstore  Boutique  Brazilian Restaurant  Breakfast Spot  Brewery  Bridge  \
0          0         0                     0               0        0       0   
1          0         0                     0               0        0       0   
2          0         0                     0               0        0       0   
3          0         0                     0               0        0       0   
4          0         0                     0               0        0       0   

   Bubble Tea Shop  Buffet  Building  Burger Joint  Burrito Place  Bus Line  \
0                0       0         0             0              0         0   
1                0       0         0             0              0         0   
2                0       0         0             0              0         0   
3                0       0         0             0              0         0   
4                0       0         0             0              0         0   

   Bus Station  Bus Stop  Business Service  Butcher  Café  Camera Store  \
0            0         0                 0        0     0             0   
1            0         0                 0        0     0             0   
2            0         1                 0        0     0             0   
3            0         0                 0        0     0             0   
4            0         0                 0        0     0             0   

   Candy Store  Caribbean Restaurant  Carpet Store  Cheese Shop  \
0            0                     0             0            0   
1            0                     0             0            0   
2            0                     0             0      

Determine the new dataframe's size

In [40]:
toronto_onehot.shape

(4733, 262)

Grouping rows by neighborhood and by taking the mean of the frequency of occurrence of each category

In [41]:
toronto_grouped = toronto_onehot.groupby('Neighborhood').mean().reset_index()
toronto_grouped

Neighborhood  Yoga Studio  \
0                                            Adelaide
     0.000000   
1                                            Agincourt     0.000000   
2                                      Agincourt North     0.000000   
3                                      Albion Gardens
     0.000000   
4                                            Alderwood     0.000000   
5                                       Bathurst Manor     0.000000   
6                                       Bathurst Quay
     0.014706   
7                                      Bayview Village     0.000000   
8                                     Beaumond Heights     0.000000   
9                                         Bedford Park     0.000000   
10                                         Berczy Park     0.000000   
11                                         Birch Cliff     0.000000   
12                                  Bloordale Gardens
     0.000000   
13                                           Brockton
     0.000000   
14   Business Reply Mail Processing Centre 969 East...     0.000000   
15                                         CFB Toronto     0.000000   
16                                            CN Tower     0.014706   
17                                         Cabbagetown     0.000000   
18                                Caledonia-Fairbanks
     0.000000   
19              Canada Post Gateway Processing Centre
     0.000000   
20                                          Cedarbrae
     0.000000   
21                                 Central Bay Street
     0.000000   
22                                           Chinatown     0.000000   
23                                           Christie
     0.000000   
24                                Church and Wellesley     0.000000   
25                                            Clairlea     0.000000   
26                                     Clarks Corners
     0.000000   
27                                          Cliffcrest     0.000000   
28                                           Cliffside     0.000000   
29                                     Cliffside West
     0.000000   
30                                         Cloverdale
     0.000000   
31                                      Commerce Court     0.000000   
32                                         Davisville
     0.000000   
33                                   Davisville North
     0.000000   
34                                           Deer Park     0.000000   
35                                            Del Ray
     0.000000   
36                                     Design Exchange     0.000000   
37                                    Don Mills North
     0.000000   
38                                    Don Mills South
     0.000000   
39                                         Dorset Park     0.000000   
40                                  Dovercourt Village     0.000000   
41                                           Downsview     0.000000   
42                                  Downsview Central
     0.000000   
43                                     Downsview East
     0.000000   
44                                    Downsview North
     0.000000   
45                                Downsview Northwest
     0.000000   
46                                      Downsview West     0.000000   
47                                           Dufferin
     0.000000   
48                               East Birchmount Park
     0.000000   
49                                        East Toronto     0.000000   
50                                               Emery     0.000000   
51                                           Eringate
     0.000000   
52                                    Exhibition Place     0.000000   
53                                           Fairview
     0.000000   
54                                First Canadian Place     0.000000   
55                                     Flemingdon Park     0.00000

Confirming new size

In [40]:
toronto_grouped.shape

(203, 262)

Render a list that includes each neighborhood along with the top 5 most common venues

In [42]:
num_top_venues = 5

for hood in toronto_grouped['Neighborhood']:
    print("----"+hood+"----")
    temp = toronto_grouped[toronto_grouped['Neighborhood'] == hood].T.reset_index()
    temp.columns = ['venue','freq']
    temp = temp.iloc[1:]
    temp['freq'] = temp['freq'].astype(float)
    temp = temp.round({'freq': 2})
    print(temp.sort_values('freq', ascending=False).reset_index(drop=True).head(num_top_venues))
    print('\n')

----Adelaide
----
         venue  freq
0  Coffee Shop  0.07
1         Café  0.06
2   Restaurant  0.05
3        Hotel  0.04
4          Gym  0.03


----Agincourt----
                 venue  freq
0        Shopping Mall  0.12
1   Chinese Restaurant  0.12
2         Skating Rink  0.06
3  Shanghai Restaurant  0.06
4     Sushi Restaurant  0.06


----Agincourt North----
                     venue  freq
0                 Pharmacy   1.0
1              Yoga Studio   0.0
2  New American Restaurant   0.0
3              Men's Store   0.0
4            Metro Station   0.0


----Albion Gardens
----
            venue  freq
0   Grocery Store  0.13
1     Coffee Shop  0.07
2  Hardware Store  0.07
3  Sandwich Place  0.07
4    Liquor Store  0.07


----Alderwood----
               venue  freq
0                Gym  0.25
1  Convenience Store  0.25
2       Dance Studio  0.25
3                Pub  0.25
4        Yoga Studio  0.00


----Bathurst Manor----
                venue  freq
0         Men's Store   1.0
1    

##### Placing this data into a new dataframe

Code a function to sort the venues in descending orider

In [43]:
def return_most_common_venues(row, num_top_venues):
    row_categories = row.iloc[1:]
    row_categories_sorted = row_categories.sort_values(ascending=False)
    
    return row_categories_sorted.index.values[0:num_top_venues]

Creating the new dataframe and display the top 10 venues for each neighborhood

In [44]:
num_top_venues = 10

indicators = ['st', 'nd', 'rd']

# create columns according to number of top venues
columns = ['Neighborhood']
for ind in np.arange(num_top_venues):
    try:
        columns.append('{}{} Most Common Venue'.format(ind+1, indicators[ind]))
    except:
        columns.append('{}th Most Common Venue'.format(ind+1))

# create a new dataframe
neighborhoods_venues_sorted = pd.DataFrame(columns=columns)
neighborhoods_venues_sorted['Neighborhood'] = toronto_grouped['Neighborhood']

for ind in np.arange(toronto_grouped.shape[0]):
    neighborhoods_venues_sorted.iloc[ind, 1:] = return_most_common_venues(toronto_grouped.iloc[ind, :], num_top_venues)

neighborhoods_venues_sorted.head()

Neighborhood 1st Most Common Venue 2nd Most Common Venue  \
0        Adelaide
           Coffee Shop                  Café   
1        Agincourt         Shopping Mall    Chinese Restaurant   
2  Agincourt North              Pharmacy         Women's Store   
3  Albion Gardens
         Grocery Store           Pizza Place   
4        Alderwood     Convenience Store          Dance Studio   

  3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
0            Restaurant                 Hotel             Gastropub   
1       Bubble Tea Shop        Discount Store          Skating Rink   
2   Dumpling Restaurant           Fish Market     Fish & Chips Shop   
3            Beer Store              Gym Pool   Fried Chicken Joint   
4                   Gym                   Pub  Fast Food Restaurant   

   6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
0         Breakfast Spot   American Restaurant      Asian Restaurant   
1  Vietnamese Restaurant   Shanghai Restaurant           Supermarket   
2                  Field  Fast Food Restaurant        Farmers Market   
3           Liquor Store  Fast Food Restaurant                  Park   
4         Farmers Market                  Farm                 Field   

  9th Most Common Venue 10th Most Common Venue  
0            Steakhouse    Japanese Restaurant  
1  Hong Kong Restaurant       Department Store  
2                  Farm     Falafel Restaurant  
3              Pharmacy            Coffee Shop  
4     Fish & Chips Shop             Donut Shop

## Cluster Neighborhoods

Run k-means to cluster the neighborhood into 5 clusters

In [45]:

# set number of clusters
kclusters = 5

toronto_grouped_clustering = toronto_grouped.drop('Neighborhood', 1)

# run k-means clustering
kmeans = KMeans(n_clusters=kclusters, random_state=0).fit(toronto_grouped_clustering)

# check cluster labels generated for each row in the dataframe
kmeans.labels_[0:10]

array([1, 1, 2, 1, 1, 3, 1, 1, 1, 1], dtype=int32)

Creating a new dataframe that includes the cluster as well as the top 10 venues for each neighborhood.

In [46]:
# add clustering labels
neighborhoods_venues_sorted.insert(0, 'Cluster Labels', kmeans.labels_)

toronto_merged = MyNeighbors

# merge toronto_grouped with toronto_data to add latitude/longitude for each neighborhood
toronto_merged = toronto_merged.join(neighborhoods_venues_sorted.set_index('Neighborhood'), on='Neighborhood')



# check the last columns!
toronto_merged.head()

PostalCode           Borough      Neighborhood   Latitude  Longitude  \
0        M3A        North York         Parkwoods  43.752420 -79.329242   
1        M4A        North York  Victoria Village  43.730600 -79.313265   
2        M5A  Downtown Toronto      Harbourfront  43.650295 -79.359166   
3        M6A        North York  Lawrence Heights  43.723270 -79.451286   
4        M6A        North York    Lawrence Manor  43.723270 -79.451286   

   Cluster Labels 1st Most Common Venue 2nd Most Common Venue  \
0             1.0              Bus Stop     Food & Drink Shop   
1             4.0         Grocery Store                  Park   
2             1.0           Coffee Shop                Bakery   
3             1.0        Clothing Store              Pharmacy   
4             1.0        Clothing Store              Pharmacy   

  3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
0                  Park    Falafel Restaurant     Electronics Store   
1         Women's Store     Electronics Store     Elementary School   
2                  Café               Theater         Boat or Ferry   
3      Toy / Game Store            Restaurant      Sushi Restaurant   
4      Toy / Game Store            Restaurant      Sushi Restaurant   

  6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
0     Elementary School   Empanada Restaurant  Ethiopian Restaurant   
1   Empanada Restaurant  Ethiopian Restaurant           Event Space   
2   Distribution Center                 Hotel        Ice Cream Shop   
3        Cosmetics Shop           Men's Store   American Restaurant   
4        Cosmetics Shop           Men's Store   American Restaurant   

    9th Most Common Venue 10th Most Common Venue  
0             Event Space          Women's Store  
1      Falafel Restaurant                   Farm  
2      Mexican Restaurant                    Spa  
3  Furniture / Home Store    Fried Chicken Joint  
4  Furniture / Home Store    Fried Chicken Joint

### Visualize the clustered results

In [47]:
# create map
map_clusters = folium.Map(location=[latitude, longitude], zoom_start=11)

# set color scheme for the clusters
x = np.arange(kclusters)
ys = [i + x + (i*x)**2 for i in range(kclusters)]
colors_array = cm.rainbow(np.linspace(0, 1, len(ys)))
rainbow = [colors.rgb2hex(i) for i in colors_array]

# add markers to the map
markers_colors = []
for lat, lon, poi, cluster in zip(toronto_merged['Latitude'], toronto_merged['Longitude'], toronto_merged['Neighborhood'], toronto_merged['Cluster Labels']):
    label = folium.Popup(str(poi) + ' Cluster ' + str(cluster), parse_html=True)
    folium.CircleMarker(
        [lat, lon],
        radius=5,
        popup=label,
        #color=rainbow[cluster-1],
        fill=True,
        #fill_color=rainbow[cluster-1],
        fill_opacity=0.7).add_to(map_clusters)
       
map_clusters

### Examine Clusters¶
Now, you can examine each cluster and determine the discriminating venue categories that distinguish each cluster. 

#### Cluster 1

In [48]:
toronto_merged.loc[toronto_merged['Cluster Labels'] == 0, toronto_merged.columns[[1] + list(range(5, toronto_merged.shape[1]))]]

Borough  Cluster Labels 1st Most Common Venue 2nd Most Common Venue  \
15   Etobicoke             0.0          Home Service         Women's Store   
16   Etobicoke             0.0          Home Service         Women's Store   
17   Etobicoke             0.0          Home Service         Women's Store   
18   Etobicoke             0.0          Home Service         Women's Store   
19   Etobicoke             0.0          Home Service         Women's Store   
97  North York             0.0      Business Service          Home Service   

   3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
15                  Farm     Electronics Store     Elementary School   
16                  Farm     Electronics Store     Elementary School   
17                  Farm     Electronics Store     Elementary School   
18                  Farm     Electronics Store     Elementary School   
19                  Farm     Electronics Store     Elementary School   
97                  Farm     Electronics Store     Elementary School   

   6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
15   Empanada Restaurant  Ethiopian Restaurant           Event Space   
16   Empanada Restaurant  Ethiopian Restaurant           Event Space   
17   Empanada Restaurant  Ethiopian Restaurant           Event Space   
18   Empanada Restaurant  Ethiopian Restaurant           Event Space   
19   Empanada Restaurant  Ethiopian Restaurant           Event Space   
97   Empanada Restaurant  Ethiopian Restaurant           Event Space   

   9th Most Common Venue 10th Most Common Venue  
15    Falafel Restaurant         Farmers Market  
16    Falafel Restaurant         Farmers Market  
17    Falafel Restaurant         Farmers Market  
18    Falafel Restaurant         Farmers Market  
19    Falafel Restaurant         Farmers Market  
97    Falafel Restaurant          Women's Store

#### Cluster 2

In [49]:
toronto_merged.loc[toronto_merged['Cluster Labels'] == 1, toronto_merged.columns[[1] + list(range(5, toronto_merged.shape[1]))]]

Borough  Cluster Labels       1st Most Common Venue  \
0          North York             1.0                    Bus Stop   
2    Downtown Toronto             1.0                 Coffee Shop   
3          North York             1.0              Clothing Store   
4          North York             1.0              Clothing Store   
5    Downtown Toronto             1.0                 Coffee Shop   
6           Etobicoke             1.0                    Pharmacy   
9          North York             1.0                Burger Joint   
10          East York             1.0                 Pizza Place   
11          East York             1.0                 Pizza Place   
12   Downtown Toronto             1.0                 Coffee Shop   
13   Downtown Toronto             1.0                 Coffee Shop   
14         North York             1.0                 Pizza Place   
20        Scarborough             1.0                         Bar   
21        Scarborough             1.0                         Bar   
22        Scarborough             1.0                         Bar   
23         North York             1.0                 Supermarket   
24         North York             1.0                 Supermarket   
25          East York             1.0                    Bus Line   
26   Downtown Toronto             1.0                 Coffee Shop   
27               York             1.0               Grocery Store   
28          Etobicoke             1.0                 Pizza Place   
29          Etobicoke             1.0                 Pizza Place   
30          Etobicoke             1.0                 Pizza Place   
31          Etobicoke             1.0                 Pizza Place   
32        Scarborough             1.0  Construction & Landscaping   
33        Scarborough             1.0  Construction & Landscaping   
34        Scarborough             1.0  Construction & Landscaping   
35       East Toronto             1.0           Health Food Store   
36   Downtown Toronto             1.0                 Coffee Shop   
37               York             1.0                        Park   
38        Scarborough             1.0           Indian Restaurant   
39          East York             1.0         Sporting Goods Shop   
40   Downtown Toronto             1.0                 Coffee Shop   
41   Downtown Toronto             1.0                        Café   
42        Scarborough             1.0                  Playground   
43         North York             1.0                     Dog Run   
47          East York             1.0                 Yoga Studio   
48   Downtown Toronto             1.0                 Coffee Shop   
49   Downtown Toronto             1.0                 Coffee Shop   
50   Downtown Toronto             1.0                 Coffee Shop   
51       West Toronto             1.0                        Park   
52       West Toronto             1.0                        Park   
53        Scarborough             1.0                  Restaurant   
54         North York             1.0              Clothing Store   
55         North York             1.0              Clothing Store   
56         North York             1.0              Clothing Store   
57         North York             1.0                 Pizza Place   
58         North York             1.0                 Pizza Place   
59          East York             1.0          Italian Restaurant   
60   Downtown Toronto             1.0             Harbor / Marina   
61   Downtown Toronto             1.0             Harbor / Marina   
62   Downtown Toronto             1.0             Harbor / Marina   
63       West Toronto             1.0                 Coffee Shop   
64       West Toronto             1.0                 Coffee Shop   
65        Scarborough             1.0                  Hobby Shop   
66        Scarborough             1.0                  Hobby Shop   
67        Scarborough             1.0                  Hobby Shop   
68         N

#### Cluster 3

In [50]:
toronto_merged.loc[toronto_merged['Cluster Labels'] == 2, toronto_merged.columns[[1] + list(range(5, toronto_merged.shape[1]))]]

Borough  Cluster Labels 1st Most Common Venue 2nd Most Common Venue  \
154  Scarborough             2.0              Pharmacy         Women's Store   
155  Scarborough             2.0              Pharmacy         Women's Store   
156  Scarborough             2.0              Pharmacy         Women's Store   
157  Scarborough             2.0              Pharmacy         Women's Store   

    3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
154   Dumpling Restaurant           Fish Market     Fish & Chips Shop   
155   Dumpling Restaurant           Fish Market     Fish & Chips Shop   
156   Dumpling Restaurant           Fish Market     Fish & Chips Shop   
157   Dumpling Restaurant           Fish Market     Fish & Chips Shop   

    6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
154                 Field  Fast Food Restaurant        Farmers Market   
155                 Field  Fast Food Restaurant        Farmers Market   
156                 Field  Fast Food Restaurant        Farmers Market   
157                 Field  Fast Food Restaurant        Farmers Market   

    9th Most Common Venue 10th Most Common Venue  
154                  Farm     Falafel Restaurant  
155                  Farm     Falafel Restaurant  
156                  Farm     Falafel Restaurant  
157                  Farm     Falafel Restaurant

#### Cluster 4

In [51]:
toronto_merged.loc[toronto_merged['Cluster Labels'] == 3, toronto_merged.columns[[1] + list(range(5, toronto_merged.shape[1]))]]

Borough  Cluster Labels 1st Most Common Venue 2nd Most Common Venue  \
44  North York             3.0           Men's Store         Women's Store   
45  North York             3.0           Men's Store         Women's Store   
46  North York             3.0           Men's Store         Women's Store   

   3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
44           Flower Shop           Fish Market     Fish & Chips Shop   
45           Flower Shop           Fish Market     Fish & Chips Shop   
46           Flower Shop           Fish Market     Fish & Chips Shop   

   6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
44                 Field  Fast Food Restaurant        Farmers Market   
45                 Field  Fast Food Restaurant        Farmers Market   
46                 Field  Fast Food Restaurant        Farmers Market   

   9th Most Common Venue 10th Most Common Venue  
44                  Farm     Falafel Restaurant  
45                  Farm     Falafel Restaurant  
46                  Farm     Falafel Restaurant

#### Cluster 5

In [52]:
toronto_merged.loc[toronto_merged['Cluster Labels'] == 4, toronto_merged.columns[[1] + list(range(5, toronto_merged.shape[1]))]]

Borough  Cluster Labels 1st Most Common Venue  \
1         North York             4.0         Grocery Store   
121  Central Toronto             4.0                  Park   
122  Central Toronto             4.0                  Park   
192        Etobicoke             4.0                  Park   
193        Etobicoke             4.0                  Park   
194        Etobicoke             4.0                  Park   

    2nd Most Common Venue 3rd Most Common Venue 4th Most Common Venue  \
1                    Park         Women's Store     Electronics Store   
121         Women's Store   Dumpling Restaurant           Fish Market   
122         Women's Store   Dumpling Restaurant           Fish Market   
192         Women's Store   Dumpling Restaurant           Fish Market   
193         Women's Store   Dumpling Restaurant           Fish Market   
194         Women's Store   Dumpling Restaurant           Fish Market   

    5th Most Common Venue 6th Most Common Venue 7th Most Common Venue  \
1       Elementary School   Empanada Restaurant  Ethiopian Restaurant   
121     Fish & Chips Shop                 Field  Fast Food Restaurant   
122     Fish & Chips Shop                 Field  Fast Food Restaurant   
192     Fish & Chips Shop                 Field  Fast Food Restaurant   
193     Fish & Chips Shop                 Field  Fast Food Restaurant   
194     Fish & Chips Shop                 Field  Fast Food Restaurant   

    8th Most Common Venue 9th Most Common Venue 10th Most Common Venue  
1             Event Space    Falafel Restaurant                   Farm  
121        Farmers Market                  Farm     Falafel Restaurant  
122        Farmers Market                  Farm     Falafel Restaurant  
192        Farmers Market                  Farm     Falafel Restaurant  
193        Farmers Market                  Farm     Falafel Restaurant  
194        Farmers Market                  Farm     Falafel Restaurant